# 2.3 stackstac으로 멀티 밴드 다루기

## Step 01. STAC API로 위성영상 검색하고 stackstac으로 열기

In [1]:
url = "https://planetarycomputer.microsoft.com/api/stac/v1"

In [2]:
from pystac_client import Client

client = Client.open(url)

In [3]:
from shapely.geometry import box

daejeon_extent = box(minx=127.277191799, maxx=127.487197090, miny=36.249605563, maxy=36.489325889)
aoi_extent = box(minx=127.3627941437947, maxx=127.40210955277311, miny=36.35998270299273, maxy=36.38934152474638)

In [4]:
aoi_extent.bounds

(127.3627941437947, 36.35998270299273, 127.40210955277311, 36.38934152474638)

In [5]:
search = client.search(max_items=100, collections="landsat-c2-l2", intersects=daejeon_extent.__geo_interface__, datetime="2024-07-01/2024-07-31")

In [6]:
items = search.item_collection()
items

In [7]:
import planetary_computer

items = planetary_computer.sign(items)

In [8]:
import stackstac

stack = stackstac.stack(items)
stack

<xarray.DataArray 'stackstac-964d79eff7ebc299fdd5d8b33cce4d86' (time: 12,
                                                                band: 19,
                                                                y: 13292,
                                                                x: 12562)>
dask.array<fetch_raster_window, shape=(12, 19, 13292, 12562), dtype=float64, chunksize=(1, 1, 1024, 1024), chunktype=numpy.ndarray>
Coordinates: (12/31)
  * time                         (time) datetime64[ns] 2024-07-04T02:10:18.29...
    id                           (time) <U31 'LC09_L2SP_116034_20240704_02_T1...
  * band                         (band) <U10 'qa' 'red' ... 'qa_aerosol'
  * x                            (x) float64 1.29e+05 1.29e+05 ... 5.058e+05
  * y                            (y) float64 4.269e+06 4.269e+06 ... 3.871e+06
    view:sun_azimuth             (time) float64 121.7 118.3 ... 124.7 125.0
    ...                           ...
    raster:bands                 (band) object {'unit': 'kelvin', 'scale': 0....
    classification:bitfields     (band) object None ... [{'name': 'fill', 'le...
    common_name                  (band) object None 'red' 'blue' ... None None
    center_wavelength            (band) object None 0.65 0.48 ... None None None
    full_width_half_max          (band) object None 0.04 0.06 ... None None None
    epsg                         int64 32652
Attributes:
    spec:        RasterSpec(epsg=32652, bounds=(128970.0, 3870570.0, 505830.0...
    crs:         epsg:32652
    transform:   | 30.00, 0.00, 128970.00|\n| 0.00,-30.00, 4269330.00|\n| 0.0...
    resolution:  30.0

In [9]:
stack = stackstac.stack(items, bounds_latlon=aoi_extent.bounds)
stack

<xarray.DataArray 'stackstac-66ee68fc0bb02e16f665582c167b2dda' (time: 8,
                                                                band: 19,
                                                                y: 112, x: 120)>
dask.array<fetch_raster_window, shape=(8, 19, 112, 120), dtype=float64, chunksize=(1, 1, 112, 120), chunktype=numpy.ndarray>
Coordinates: (12/31)
  * time                         (time) datetime64[ns] 2024-07-04T02:10:42.18...
    id                           (time) <U31 'LC09_L2SP_116035_20240704_02_T1...
  * band                         (band) <U10 'qa' 'red' ... 'qa_aerosol'
  * x                            (x) float64 3.531e+05 3.531e+05 ... 3.567e+05
  * y                            (y) float64 4.028e+06 4.028e+06 ... 4.025e+06
    view:sun_azimuth             (time) float64 118.3 118.5 ... 124.7 125.0
    ...                           ...
    raster:bands                 (band) object {'unit': 'kelvin', 'scale': 0....
    classification:bitfields     (band) object None ... [{'name': 'fill', 'le...
    common_name                  (band) object None 'red' 'blue' ... None None
    center_wavelength            (band) object None 0.65 0.48 ... None None None
    full_width_half_max          (band) object None 0.04 0.06 ... None None None
    epsg                         int64 32652
Attributes:
    spec:        RasterSpec(epsg=32652, bounds=(353100.0, 4025040.0, 356700.0...
    crs:         epsg:32652
    transform:   | 30.00, 0.00, 353100.00|\n| 0.00,-30.00, 4028400.00|\n| 0.0...
    resolution:  30.0

In [10]:
rgb = stack.sel(band=["red", "green", "blue"])
rgb

<xarray.DataArray 'stackstac-66ee68fc0bb02e16f665582c167b2dda' (time: 8,
                                                                band: 3,
                                                                y: 112, x: 120)>
dask.array<getitem, shape=(8, 3, 112, 120), dtype=float64, chunksize=(1, 1, 112, 120), chunktype=numpy.ndarray>
Coordinates: (12/31)
  * time                         (time) datetime64[ns] 2024-07-04T02:10:42.18...
    id                           (time) <U31 'LC09_L2SP_116035_20240704_02_T1...
  * band                         (band) <U10 'red' 'green' 'blue'
  * x                            (x) float64 3.531e+05 3.531e+05 ... 3.567e+05
  * y                            (y) float64 4.028e+06 4.028e+06 ... 4.025e+06
    view:sun_azimuth             (time) float64 118.3 118.5 ... 124.7 125.0
    ...                           ...
    raster:bands                 (band) object {'scale': 2.75e-05, 'nodata': ...
    classification:bitfields     (band) object None None None
    common_name                  (band) object 'red' 'green' 'blue'
    center_wavelength            (band) object 0.65 0.56 0.48
    full_width_half_max          (band) object 0.04 0.06 0.06
    epsg                         int64 32652
Attributes:
    spec:        RasterSpec(epsg=32652, bounds=(353100.0, 4025040.0, 356700.0...
    crs:         epsg:32652
    transform:   | 30.00, 0.00, 353100.00|\n| 0.00,-30.00, 4028400.00|\n| 0.0...
    resolution:  30.0

In [12]:
import dask.diagnostics

with dask.diagnostics.ProgressBar():
    rgb = rgb.compute()

rgb.plot.imshow(row="time", rgb="band", robust=True, size=6)

Error in callback <function _draw_all_if_interactive at 0x1780b8700> (for post_execute), with arguments args (),kwargs {}:


ValueError: object __array__ method not producing an array

ValueError: object __array__ method not producing an array

<Figure size 700x4800 with 8 Axes>

## Step 03. NDVI 만들기